In [3]:
import json
from collections import defaultdict

# Load the original annotated graph
with open("annotated_human_graph.json", "r") as f:
    graph = json.load(f)

nodes = {n["id"]: {**n, "children": []} for n in graph["nodes"]}
links = graph["links"]

# Build child-parent relationships
for link in links:
    src = link["source"]
    tgt = link["target"]
    if src not in nodes:
        nodes[src] = {"id": src, "label": src, "children": []}
    if tgt not in nodes:
        nodes[tgt] = {"id": tgt, "label": tgt, "children": []}
    nodes[src]["children"].append(nodes[tgt])

# Identify root nodes (those that are never targets)
all_targets = {link["target"] for link in links}
roots = [node for node_id, node in nodes.items() if node_id not in all_targets]
approved_roots = [
    "http://purl.obolibrary.org/obo/GO_0003674", # Molecular Function
    "http://purl.obolibrary.org/obo/GO_0005575", # Cellular Component
    "http://purl.obolibrary.org/obo/GO_0008150", # Biological Function
]
roots = [node for node in roots if node["id"] in approved_roots]  # Filter out nodes without labels
print(roots[:10])

def transform_for_jstree(node):
    return {
        "text": node.get("label", node["id"]),
        "data": {
            "definition": node.get("definition", ""),
            "id": node["id"],
            "job_suggestion": node.get("job_suggestion", "")
        },
        "children": [transform_for_jstree(child) for child in node["children"]]
    }


tree_data = [transform_for_jstree(root) for root in roots]

# Save the transformed tree data to a file
with open("html_ready_human_go_tree.json", "w") as f:
    json.dump(tree_data, f, indent=2)

print("Converted tree saved as go_tree.json")


[{'label': 'molecular_function', 'definition': 'A molecular process that can be carried out by the action of a single macromolecular machine, usually via direct physical interactions with other molecular entities. Function in this sense denotes an action, or activity, that a gene product (or a complex) performs.', 'parents': [], 'job_suggestion': 'engineer/craftsman/technician/laborer', 'id': 'http://purl.obolibrary.org/obo/GO_0003674', 'children': [{'label': 'cytoskeletal motor activity', 'definition': 'Generation of force resulting in movement, for example along a microfilament or microtubule, or in torque resulting in membrane scission or rotation of a flagellum. The energy required is obtained either from the hydrolysis of a nucleoside triphosphate or by an electrochemical proton gradient (proton-motive force).', 'parents': ['molecular_function which was defined as engineer/craftsman/technician/laborer'], 'job_suggestion': 'construction equipment/freight transport/transportation', 